<a href="https://colab.research.google.com/github/NolanSmyth/deepMIDI/blob/master/midiMusic.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Dependences

In [37]:
# Import Tensorflow 2.0
%tensorflow_version 2.x
import tensorflow as tf 

import numpy as np
import os
import glob
from tqdm import tqdm
from keras.models import Sequential
from keras.layers import Dense
from keras.layers import Dropout
from keras.layers import LSTM
from keras.layers import Activation
from keras.utils import np_utils
from keras.callbacks import ModelCheckpoint
from keras.utils import np_utils
from music21 import *

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [153]:
path = '/content/drive/My Drive/midi/*.mid'
def get_notes(path):

  ''' extracts all notes from midi files stored in drive given
  path (str) - path location 

  returns
  notes - list of all notes from all midi files
  '''

  notes = []
  midfs = glob.glob(path)
  for midf in midfs:
    midi_notes = converter.parse(midf)
  notes_to_parse = midi_notes.flat.notes
  for element in notes_to_parse:
    if isinstance(element, note.Note):
      notes.append(str(element.pitch))
    elif isinstance(element, note.Chord):
      notes.append('.'.join(str(n) for n in element.normalOrder))

  return notes  
notes = get_notes(path)

In [6]:
# create a dictionary mapping each name to a unique integer
pitch_names = sorted(set(notes))
note_to_int = {note:i for i, note in enumerate(pitch_names)}

# create mapping from indices back to note name
int_to_note = np.array(pitch_names)

num_unique_notes = len(pitch_names)
print('There are', num_unique_notes, 'unique characters in the dataset')

There are 42 unique characters in the dataset


In [7]:
def vectorize_notes(notes):
  # get names of all pitches used
  
  vectorized_notes = np.array([note_to_int[note] for note in notes])
  return vectorized_notes
vectorized_notes = vectorize_notes(notes)

In [8]:
print ('{} ---- characters mapped to int ----> {}'.format(repr(notes[:10]), vectorized_notes[:10]))

['D4', 'A4', 'F4', 'D4', 'C#4', 'D4', 'E4', 'F4', 'G4', 'F4'] ---- characters mapped to int ----> [19  2 34 19 12 19 26 34 40 34]


In [16]:
def get_batch(vectorized_notes, seq_length, batch_size):

  ''' create training exmaples for LSTM given
  vectorized_notes - a list ints representing all the notes from inputed midi files
  seq_length - length of each training sequence
  batch_size - size of each batch

  returns:
  x_batch - inputs
  y_batch - true labels for training
  '''

  # length of vectorized notes
  n = vectorized_notes.shape[0] - 1
  # randomly choose starting indices for the examples in training batch
  idx = np.random.choice(n - seq_length, batch_size)

  # create input and output sequences to feed into neural net
  input_batch = [vectorized_notes[i : i+seq_length] for i in idx]
  output_batch = [vectorized_notes[i+1 : i+seq_length+1] for i in idx]
  
  x_batch = np.reshape(input_batch, [batch_size, seq_length])
  y_batch = np.reshape(output_batch, [batch_size, seq_length])

  return x_batch, y_batch



In [68]:
x_batch, y_batch = get_batch(vectorized_notes, seq_length=5, batch_size=1)

for i, (input_idx, target_idx) in enumerate(zip(np.squeeze(x_batch), np.squeeze(y_batch))):
    print("Step {:3d}".format(i))
    print("  input: {} ({:s})".format(input_idx, repr(int_to_note[input_idx])))
    print("  expected output: {} ({:s})".format(target_idx, repr(int_to_note[target_idx])))

Step   0
  input: 20 ('D5')
  expected output: 33 ('F3')
Step   1
  input: 33 ('F3')
  expected output: 16 ('C5')
Step   2
  input: 16 ('C5')
  expected output: 40 ('G4')
Step   3
  input: 40 ('G4')
  expected output: 39 ('G3')
Step   4
  input: 39 ('G3')
  expected output: 10 ('B4')


In [69]:
def LSTM(rnn_units): 
  return tf.keras.layers.LSTM(
    rnn_units, 
    return_sequences=True, 
    recurrent_initializer='glorot_uniform',
    recurrent_activation='sigmoid',
    stateful=True,
  )

In [70]:
def create_network(num_unique_notes, embedding_dim, rnn_units, batch_size):
  ''' create the structure of the neural network given
  net_in - input for LSTM
  net_out - output for LSTM
  '''

  model = tf.keras.Sequential([
  tf.keras.layers.Embedding(num_unique_notes, embedding_dim, batch_input_shape=[batch_size, None]),
  LSTM(rnn_units), 
  tf.keras.layers.Dense(num_unique_notes)
  ])

  return model

In [71]:
model = create_network(num_unique_notes, embedding_dim=256, rnn_units=512, batch_size=32)
model.summary()

Model: "sequential_15"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_15 (Embedding)     (32, None, 256)           10752     
_________________________________________________________________
lstm_15 (LSTM)               (32, None, 512)           1574912   
_________________________________________________________________
dense_15 (Dense)             (32, None, 42)            21546     
Total params: 1,607,210
Trainable params: 1,607,210
Non-trainable params: 0
_________________________________________________________________


In [72]:
x, y = get_batch(vectorized_notes, seq_length=10, batch_size=32)
pred = model(x)
print("Input shape:      ", x.shape, " # (batch_size, sequence_length)")
print("Prediction shape: ", pred.shape, "# (batch_size, sequence_length, vocab_size)")


Input shape:       (32, 10)  # (batch_size, sequence_length)
Prediction shape:  (32, 10, 42) # (batch_size, sequence_length, vocab_size)


In [73]:
sampled_indices = tf.random.categorical(pred[0], num_samples=1)
sampled_indices = tf.squeeze(sampled_indices,axis=-1).numpy()
sampled_indices


array([13, 33, 33, 35, 35, 15,  9, 38, 27,  5])

In [98]:
print("Input: \n", repr("".join(int_to_note[x[0]])))
print()
print("Next Char Predictions: \n", repr("".join(int_to_note[sampled_indices])))

Input: 
 'A4D4D3A3D4F4E4A3B3E5'

Next Char Predictions: 
 'C#5 F3 F3 F5 F5 C4 B3 G2 E5 B-3'


In [75]:
def compute_loss(labels, logits):
  loss = tf.keras.losses.sparse_categorical_crossentropy(labels, logits, from_logits=True)
  return loss

example_batch_loss = compute_loss(y, pred)
# example_batch_loss = compute_loss('''TODO''', '''TODO''') # TODO

print("Prediction shape: ", pred.shape, " # (batch_size, sequence_length, vocab_size)") 
print("scalar_loss:      ", example_batch_loss.numpy().mean())

Prediction shape:  (32, 10, 42)  # (batch_size, sequence_length, vocab_size)
scalar_loss:       3.737566


In [177]:
### Hyperparameter setting and optimization ###

# Optimization parameters:
num_training_iterations = 1000  # Increase this to train longer
batch_size = 10  # Experiment between 1 and 64
seq_length = 20  # Experiment between 50 and 500
learning_rate = 5e-3  # Experiment between 1e-5 and 1e-1

# Model parameters: 
vocab_size = len(pitch_names)
embedding_dim = 64 
rnn_units = 512  # Experiment between 1 and 2048

# Checkpoint location: 
checkpoint_dir = './training_checkpoints'
checkpoint_prefix = os.path.join(checkpoint_dir, "my_ckpt")

In [178]:
model = create_network(vocab_size, embedding_dim, rnn_units, batch_size)

optimizer = tf.keras.optimizers.Adam(learning_rate)

@tf.function
def train_step(x, y): 
  # Use tf.GradientTape()
  with tf.GradientTape() as tape:
  
    y_hat = model(x) 
  
    loss = compute_loss(y, y_hat) 

  # Now, compute the gradients 
  grads = tape.gradient(loss, model.trainable_variables) # TODO
  
  # Apply the gradients to the optimizer so it can update the model accordingly
  optimizer.apply_gradients(zip(grads, model.trainable_variables))
  return loss

##################
# Begin training!#
##################

history = []
if hasattr(tqdm, '_instances'): tqdm._instances.clear() # clear if it exists

for iter in tqdm(range(num_training_iterations)):

  # Grab a batch and propagate it through the network
  x_batch, y_batch = get_batch(vectorized_notes, seq_length, batch_size)
  loss = train_step(x_batch, y_batch)

  # Update the progress bar
  history.append(loss.numpy().mean())

  # Update the model with the changed weights!
  if iter % 100 == 0:     
    model.save_weights(checkpoint_prefix)
    
# Save the trained model and the weights
model.save_weights(checkpoint_prefix)

100%|██████████| 1000/1000 [00:05<00:00, 185.77it/s]


In [179]:
model = create_network(vocab_size, embedding_dim, rnn_units, batch_size=1) 

# Restore the model weights for the last checkpoint after training
model.load_weights(tf.train.latest_checkpoint(checkpoint_dir))
model.build(tf.TensorShape([1, None]))

model.summary()

Model: "sequential_21"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_21 (Embedding)     (1, None, 64)             2688      
_________________________________________________________________
lstm_21 (LSTM)               (1, None, 512)            1181696   
_________________________________________________________________
dense_21 (Dense)             (1, None, 42)             21546     
Total params: 1,205,930
Trainable params: 1,205,930
Non-trainable params: 0
_________________________________________________________________


In [180]:
def generate_text(model, start_string, generation_length=100):

  input_eval = [note_to_int[s] for s in start_string.split()]
  input_eval = tf.expand_dims(input_eval,0)

  text_generated = []

  model.reset_states()
  tqdm._instances.clear()

  for i in tqdm(range(generation_length)):
      predictions = model(input_eval)
      
      # Remove the batch dimension
      predictions = tf.squeeze(predictions, 0)
      
      predicted_id = tf.random.categorical(predictions, num_samples=1)[-1,0].numpy()
      
      # Pass the prediction along with the previous hidden state
      #   as the next inputs to the model
      input_eval = tf.expand_dims([predicted_id], 0)
      
      text_generated.append(int_to_note[predicted_id]) # TODO 
      # text_generated.append('''TODO''')
    
  return (start_string + ' '.join(text_generated))

In [198]:
generated_text = generate_text(model, start_string="A4 ", generation_length=50)

100%|██████████| 50/50 [00:00<00:00, 212.42it/s]


In [197]:
def create_midi(generated_text):
  '''Converts the output from the prediction into notes and then creates a midi 
  file from the notes

  returns Stream
  '''

  offset = 0 #may change this later
  output_notes = []

  for pattern in generated_text:
    new_note = note.Note(pattern)
    new_note.offset = offset
    output_notes.append(new_note)
    offset += .5

  midi_stream = stream.Stream(output_notes)
  return midi_stream

In [ ]:
#To play midi in notebook
!apt install fluidsynth
!cp /usr/share/sounds/sf2/FluidR3_GM.sf2 ./font.sf2
!pip install midi2audio
from midi2audio import FluidSynth
from IPython.display import Audio

In [172]:
#from first original midi file loaded
midi_orig_test = create_midi(notes[0:100])
midi_orig_test.write('midi', fp='orig_output.mid')

'orig_output.mid'

In [199]:
#output
midi_stream = create_midi(generated_text.split())
midi_stream.write('midi', fp='test_output.mid')

'test_output.mid'

In [173]:
FluidSynth("font.sf2").midi_to_audio('orig_output.mid', 'test_orig.wav')
Audio("test_orig.wav")

In [200]:
FluidSynth("font.sf2").midi_to_audio('test_output.mid', 'test.wav')
Audio("test.wav")